## New attempt

In the end, we have an HDF file of GlaThiDa per RGI sub-region.

In [1]:
import pandas as pd
import geopandas as gpd
import shapely.geometry as shpg
import numpy as np
import os
import progressbar
import time
from oggm import utils, cfg

In [2]:
gtd_dir = './glathida-v3.1.0/data'
# gtd_dir = './GlaThiDa_2016'

## Read the files

In [3]:
df = pd.read_csv(os.path.join(gtd_dir, 'TTT.csv'), dtype={'SURVEY_DATE': 'str'}, low_memory=False)

In [4]:
for c in df:
    print(c, df[c].dtype)

GlaThiDa_ID int64
POLITICAL_UNIT object
GLACIER_NAME object
SURVEY_DATE object
PROFILE_ID object
POINT_ID object
POINT_LAT float64
POINT_LON float64
ELEVATION float64
THICKNESS int64
THICKNESS_UNCERTAINTY float64
DATA_FLAG float64
REMARKS object


In [5]:
len(df)

3854279

In [6]:
len(df.loc[df.THICKNESS == 0]) / len(df), len(df.loc[df.THICKNESS == 0])

(0.04538540152386478, 174928)

In [7]:
# Replace with 62 when available
rgi_reg = gpd.read_file(os.path.join(utils.get_rgi_dir('62'), '00_rgi62_regions/00_rgi62_O1Regions.shp'))

## Convert lon, lat to Point geometries 

In [8]:
geoms = []
for lon, lat in progressbar.progressbar(zip(df.POINT_LON, df.POINT_LAT), max_value=len(df)):
    geoms.append(shpg.Point(lon, lat))

100% (3854279 of 3854279) |##############| Elapsed Time: 0:00:25 Time:  0:00:25


In [9]:
df['geometry'] = geoms

In [10]:
df = gpd.GeoDataFrame(df)

## Read RGI

In [62]:
rdf = []
for reg in range(1, 20):
    rdf.append(gpd.read_file(utils.get_rgi_region_file(f'{reg:02d}', version='70G')))
rdf = pd.concat(rdf)

In [63]:
df.crs = rdf.crs

In [64]:
len(df), len(rdf)

(3854279, 274531)

In [65]:
joined = gpd.sjoin(df, rdf, how='left', predicate='within')

In [66]:
len(joined), len(joined.loc[joined.rgi_id.isnull()])

(3854279, 265675)

In [67]:
no_join = joined.loc[joined.rgi_id.isnull()]
ok_join = joined.loc[~joined.rgi_id.isnull()]

In [68]:
len(ok_join) / len(df)

0.9310701171347482

In [69]:
ok_join.iloc[:2].T

0  \
GlaThiDa_ID                                        33   
POLITICAL_UNIT                                     US   
GLACIER_NAME                                   EASTON   
SURVEY_DATE                                  19929999   
PROFILE_ID                                        NaN   
POINT_ID                                            1   
POINT_LAT                                    48.76738   
POINT_LON                                 -121.819644   
ELEVATION                                      2962.0   
THICKNESS                                           0   
THICKNESS_UNCERTAINTY                             NaN   
DATA_FLAG                                         NaN   
REMARKS                                           NaN   
geometry               POINT (-121.819644 48.7673801)   
index_right                                   15002.0   
rgi_id                        RGI2000-v7.0-G-02-15003   
o1region                                           02   
o2region                                        02-04   
glims_id                               G238158E48759N   
anlys_id                                     761915.0   
subm_id                                         744.0   
src_date                          1975-09-09T00:00:00   
cenlon                                    -121.844147   
cenlat                                      48.758784   
utm_zone                                         10.0   
area_km2                                     4.995923   
primeclass                                        0.0   
conn_lvl                                          0.0   
surge_type                                        0.0   
term_type                                         9.0   
glac_name                              Deming Glacier   
is_rgi6                                           1.0   
termlon                                   -121.868505   
termlat                                     48.741924   
zmin_m                                      1179.0857   
zmax_m                                      3273.7449   
zmed_m                                      2251.0093   
zmean_m                                      2254.844   
slope_deg                                   23.269547   
aspect_deg                                  217.05867   
aspect_sec                                        6.0   
dem_source                                   COPDEM30   
lmax_m                                         5346.0   

                                                     1  
GlaThiDa_ID                                         33  
POLITICAL_UNIT                                      US  
GLACIER_NAME                                    EASTON  
SURVEY_DATE                                   19929999  
PROFILE_ID                                         NaN  
POINT_ID                                             2  
POINT_LAT                                    48.764904  
POINT_LON                                  -121.821909  
ELEVATION                                       2813.0  
THICKNESS                                           29  
THICKNESS_UNCERTAINTY                              NaN  
DATA_FLAG                                          NaN  
REMARKS                                            NaN  
geometry               POINT (-121.8219093 48.7649042)  
index_right                                    15001.0  
rgi_id                         RGI2000-v7.0-G-02-15002  
o1region                                            02  
o2region                                         02-04  
glims_id                                G238169E48750N  
anlys_id                                      761926.0  
subm_id                                          744.0  
src_date                           1974-09-09T00:00:00  
cenlon                                     -121.830812  
cenlat                                       48.749909  
utm_zone                                          10.0  
area_km2                                      2.887898  
prim

In [70]:
ok_join = ok_join[np.append(ok_join.columns[:13], ok_join.columns[15:16])]

In [71]:
ok_join.to_hdf('glathida-v3.1.0/data/TTT_RGI_v70G.h5', key='data')

/tmp/ipykernel_4126691/2178455800.py:1: PerformanceWarning: 
your performance may suffer as PyTables will pickle object types that it cannot
map directly to c-types [inferred_type->mixed,key->block1_values] [items->Index(['POLITICAL_UNIT', 'GLACIER_NAME', 'SURVEY_DATE', 'PROFILE_ID',
       'POINT_ID', 'REMARKS', 'rgi_id'],
      dtype='object')]

  ok_join.to_hdf('glathida-v3.1.0/data/TTT_RGI_v70G.h5', key='data')


In [72]:
import warnings
import tables

In [73]:
file = 'glathida-v3.1.0/data/TTT_RGI_v70G_per_id.h5'
if os.path.exists(file):
    os.remove(file)

rids = ok_join.rgi_id.unique()
for rid in rids:
    tt = ok_join.loc[ok_join.rgi_id == rid]
    with warnings.catch_warnings():
        warnings.simplefilter('ignore', tables.NaturalNameWarning)
        tt.to_hdf(file, key=rid, append=True, complevel=5)

In [48]:
def get_rids():
    with pd.HDFStore('glathida-v3.1.0/data/TTT_RGI_v70C_per_id.h5') as store:
        rgi_ids = list(store.keys())
        return np.array([s[1:] for s in rgi_ids])

In [49]:
%timeit get_rids()

946 ms ± 10.5 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


In [74]:
def read_data(rid):
    out = None
    try:
        out = pd.read_hdf('glathida-v3.1.0/data/TTT_RGI_v70C_per_id.h5', key=rid)
    except KeyError:
        pass
    return out

In [60]:
%timeit read_data('RGI2000-v7.0-C-02-10810')

16.5 ms ± 218 µs per loop (mean ± std. dev. of 7 runs, 100 loops each)


In [61]:
%timeit read_data('RGI2000-v7.0-C-02-10812')

503 µs ± 11.3 µs per loop (mean ± std. dev. of 7 runs, 1,000 loops each)


In [33]:
t = pd.read_hdf('glathida-v3.1.0/data/TTT_RGI_v70C.h5')

In [39]:
%timeit  pd.read_hdf('glathida-v3.1.0/data/TTT_RGI_v70C.h5')

1.96 s ± 99.2 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


In [35]:
%timeit t.loc[t.rgi_id == 'RGI2000-v7.0-C-02-10810']

191 ms ± 8.26 ms per loop (mean ± std. dev. of 7 runs, 10 loops each)


In [37]:
%timeit t.loc[t.rgi_id == 'RGI2000-v7.0-C-02-10210']

192 ms ± 5.84 ms per loop (mean ± std. dev. of 7 runs, 10 loops each)


In [38]:
t.loc[t.rgi_id == 'RGI2000-v7.0-C-02-10810']

GlaThiDa_ID POLITICAL_UNIT    GLACIER_NAME SURVEY_DATE PROFILE_ID  \
0               33             US          EASTON    19929999        NaN   
1               33             US          EASTON    19929999        NaN   
2               33             US          EASTON    19929999        NaN   
3               33             US          EASTON    19929999        NaN   
4               33             US          EASTON    19929999        NaN   
...            ...            ...             ...         ...        ...   
19089          502             US  SHERMAN CRATER    20109999        NaN   
19090          502             US  SHERMAN CRATER    20109999        NaN   
19091          502             US  SHERMAN CRATER    20109999        NaN   
19092          502             US  SHERMAN CRATER    20109999        NaN   
19093          502             US  SHERMAN CRATER    20109999        NaN   

      POINT_ID  POINT_LAT   POINT_LON  ELEVATION  THICKNESS  \
0            1  48.767380 -121.819644     2962.0          0   
1            2  48.764904 -121.821909     2813.0         29   
2            3  48.761662 -121.825264     2598.0         41   
3            4  48.757063 -121.829107     2383.0         71   
4            5  48.753715 -121.832006     2284.0         82   
...        ...        ...         ...        ...        ...   
19089       76  48.768840 -121.816270     2931.0         59   
19090       77  48.768892 -121.816151     2928.0         54   
19091       78  48.768944 -121.816032     2926.0         51   
19092       79  48.768990 -121.815914     2923.0         49   
19093       80  48.769043 -121.815795     2921.0         43   

       THICKNESS_UNCERTAINTY  DATA_FLAG REMARKS                   rgi_id  
0                        NaN        NaN     NaN  RGI2000-v7.0-C-02-10810  
1                        NaN        NaN     NaN  RGI2000-v7.0-C-02-10810  
2                        NaN        NaN     NaN  RGI2000-v7.0-C-02-10810  
3                        NaN        NaN     NaN  RGI2000-v7.0-C-02-10810  
4                        NaN        NaN     NaN  RGI2000-v7.0-C-02-10810  
...                      ...        ...     ...                      ...  
19089                    5.0        NaN     NaN  RGI2000-v7.0-C-02-10810  
19090                    5.0        NaN     NaN  RGI2000-v7.0-C-02-10810  
19091                    5.0        NaN     NaN  RGI2000-v7.0-C-02-10810  
19092                    5.0        NaN     NaN  RGI2000-v7.0-C-02-10810  
19093                    5.0        NaN     NaN  RGI2000-v7.0-C-02-10810  

[2533 rows x 14 columns]

## Add the RGI Region attribute 

In [9]:
reg = np.ones(len(df), dtype=int) * -1
prev_reg = None
for i, p in progressbar.progressbar(enumerate(df.geometry), max_value=len(df)):
    if prev_reg is not None and prev_reg.contains(p):
        reg[i] = reg[i-1]
        continue
    try:
        sel = rgi_reg.loc[rgi_reg.contains(p)].iloc[0]
        reg[i] = sel.RGI_CODE
        prev_reg = sel.geometry
    except:
        prev_reg = None

100% (3854279 of 3854279) |##############| Elapsed Time: 0:01:44 Time:  0:01:44


In [10]:
df['RGI_REG'] = reg
sorted(df['RGI_REG'].unique())

[1, 2, 3, 4, 5, 7, 8, 10, 11, 12, 13, 16, 17, 18, 19]

## Separate the data in RGI Regions

In [11]:
dfs = OrderedDict()
for r in sorted(df['RGI_REG'].unique()):
    dfs[r] = df.loc[df.RGI_REG == r].copy()

### Prepare for writing and write to file 

In [12]:
for i, (k, d) in enumerate(dfs.items()):
    d.drop(['geometry'], axis=1, inplace=True)
    d['RGI_REG'] = d['RGI_REG'].astype(str)
    d['ELEVATION'] = d['ELEVATION'].astype(str)

In [13]:
for c in d:
    print(c, d[c].dtype)

GlaThiDa_ID int64
POLITICAL_UNIT object
GLACIER_NAME object
SURVEY_DATE object
PROFILE_ID object
POINT_ID object
POINT_LAT float64
POINT_LON float64
ELEVATION object
THICKNESS int64
THICKNESS_UNCERTAINTY float64
DATA_FLAG float64
REMARKS object
RGI_REG object


In [14]:
outf = os.path.join(gtd_dir, 'TTT_per_reg.h5')
if os.path.exists(outf):
    os.remove(outf)
count = 0
for i, (k, d) in enumerate(dfs.items()):
    key = '{:02d}'.format(int(k))
    print('Writing', key, len(d))
    with warnings.catch_warnings():
        warnings.simplefilter('ignore', tables.NaturalNameWarning)
        d.to_hdf(outf, key, append=True, complevel=5)
        count += len(d)
assert count == len(df)

Writing 01 87157
Writing 02 3406
Writing 03 868346
Writing 04 309453
Writing 05 557136
Writing 07 966408
Writing 08 10801
Writing 10 7726
Writing 11 478312
Writing 12 2278
Writing 13 15327
Writing 16 1287
Writing 17 8463
Writing 18 619
Writing 19 537560
